In [1]:
# imports
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json
import os
import plotly.express as px
import requests

# Foursquare

Send a request to Foursquare with a small radius (1000m) for all the bike stations in your city of choice. 

In [2]:
FSQ_KEY = os.getenv('FOURSQUARE_API_KEY')

In [3]:
FSQ_KEY = 'fsq3BQAqUk8AGjMKyi9vaiYy0SOlZ4gZUueUDBhYPCKo42k='

In [4]:
# Define function call
def fs_call(query,latitude,longitude,radius):
    import requests

    url = f"https://api.foursquare.com/v3/places/search?query={query}&ll={latitude}%2C{longitude}&radius={radius}&limit=50"

    headers = {
        "Accept": "application/json",
        "Authorization": FSQ_KEY
    }

    params = {
        "query": query,
        "ll": f'{latitude},{longitude}',
        "radius": radius,
        "sort": "DISTANCE"
    }

    response = requests.request("GET", url, params=params, headers=headers)

    data = response.json()
    
    return data

In [5]:
# Sample

In [6]:
sample_data = fs_call('bar',47.606,-122.349358,1000)
sample_data['results'][0]

{'fsq_id': '4fbfa89ee4b0fddeca5b5cef',
 'categories': [{'id': 10001,
   'name': 'Amusement Park',
   'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/themepark_',
    'suffix': '.png'}}],
 'chains': [],
 'distance': 513,
 'geocodes': {'main': {'latitude': 47.605993, 'longitude': -122.341159},
  'roof': {'latitude': 47.605993, 'longitude': -122.341159}},
 'link': '/v3/places/4fbfa89ee4b0fddeca5b5cef',
 'location': {'address': '1301 Alaskan Way',
  'census_block': '530330081013017',
  'country': 'US',
  'cross_street': 'Pier 57',
  'dma': 'Seattle-Tacoma',
  'formatted_address': '1301 Alaskan Way (Pier 57), Seattle, WA 98101',
  'locality': 'Seattle',
  'postcode': '98101',
  'region': 'WA'},
 'name': 'Seattle Great Wheel',
 'related_places': {'parent': {'fsq_id': '4b5fbee2f964a5200bcb29e3',
   'name': 'Pier 57'}},
 'timezone': 'America/Los_Angeles'}

In [7]:
context = sample_data['context']
context
geo_bounds = context['geo_bounds']
geo_bounds
circle = geo_bounds['circle']
circle
center = circle['center']
center
search_latitude = center['latitude']
search_latitude
search_longitude = center['longitude']

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [8]:
df_to_bikes = pd.read_csv('df_bikes.csv')

In [9]:
def parse_fs_search(data):
    results = data['results']
    search_results_list = []
    i = 0
    for result in results:
        result = results[i]
        # Define result variables 
        fsq_id = result['fsq_id']


        # # Loop to check for multiple categories
        categories = result['categories']
        if len(categories) == 0:
            category_name = 'N/A'
        else:
            category_name = categories[0]['name']
            
        
        # # category_names = []
        # # i = 0
        # # for category in categories:
        # #     category_name = categories[0]['name']
        # #     category_names.append(category_name)
        # #     i += 1

        distance = result['distance']


        geocodes = result['geocodes']

        result_latitude = geocodes['main']['latitude']
        result_longitude = geocodes['main']['longitude']


        link = result['link']


        location = result['location']
        country = location['country']
        formatted_address = location['formatted_address']
        if 'locality' in location:
            locality = location['locality']
            city = locality
        else:
            city = 'N/A'
        if 'region' in location:
            region = location['region']
        else:
            region = 'N/A'

        name = result['name']
        
        # Define context variables
        context = data['context']
        geo_bounds = context['geo_bounds']
        circle = geo_bounds['circle']
        center = circle['center']
        search_latitude = center['latitude']
        search_longitude = center['longitude']
        
        # Create dictionary for business listing
        result_dict = {'name' : name, 
                       'category' : category_name, 
                       'city' : city, 
                       'region' : region, 
                       'country' : country, 
                       'latitude' : result_latitude, 
                       'longitude' : result_longitude,
                       'distance' : distance,
                       'search_latitude' : search_latitude,
                       'search_longitude' : search_longitude}

        search_results_list.append(result_dict)
        
        i += 1

    return search_results_list

In [10]:
# Use Bixi location to initiate search

# Empty list to contain result dataframes
all_search_results_list = []

# List from bixi dataframe
bixi_lats = df_to_bikes['latitude'].to_list()
bixi_longs = df_to_bikes['longitude'].to_list()

i=0

# For each bike station
for lat in bixi_lats:
    # Set lat and long to lat and long of current station
    bixi_lat = bixi_lats[i]
    bixi_long = bixi_longs[i]

    query = 'bar'

    radius = 1000
    
    # Call API for each station's set of lat,long
    data = fs_call(query,bixi_lat,bixi_long,radius)
    
    # Parse search results data
    search_results = parse_fs_search(data)
    
    # Convert search result to dataframe
    df_search_results = pd.DataFrame(search_results)
    
    # Append search dataframe to list of all search dataframes
    all_search_results_list.append(df_search_results)

    i += 1



In [11]:
def parse_fs_search(data):
    if 'results' in data:
        results = data['results']
        # rest of the code
    else:
        print("Results key not found in data")
        return []

parse_fs_search(data)

In [12]:
# Concatenate all search results to single dataframe

df_foursquare_listings = pd.concat(all_search_results_list)
df_fs = df_foursquare_listings.reset_index(drop=True)
df_fs.rename(columns={'distance_from_bike_station':'dist_from_station_m'})

name                category     city region  \
0         Leslieville Farmers Market          Farmers Market  Toronto     ON   
1                         McDonald's            Burger Joint  Toronto     ON   
2                   T.O. Ceviche Bar     Peruvian Restaurant  Toronto     ON   
3                  Chalet Beauty Bar              Hair Salon  Toronto     ON   
4                        Chick-N-Joy                   Diner  Toronto     ON   
...                              ...                     ...      ...    ...   
32158                   Dog Fountain                Fountain  Toronto     ON   
32159     The Omni King Edward Hotel                   Hotel  Toronto     ON   
32160  Metropolitan Restaurant & Bar                   Diner  Toronto     ON   
32161                    Consort Bar  Arts and Entertainment  Toronto     ON   
32162                    Berczy Park              Urban Park  Toronto     ON   

      country   latitude  longitude  distance  search_latitude  \
0          CA  43.664679 -79.319687        40        43.665269   
1          CA  43.665065 -79.319000        62        43.665269   
2          CA  43.665973 -79.318863       108        43.665269   
3          CA  43.665973 -79.318863       108        43.665269   
4          CA  43.665121 -79.321347       129        43.665269   
...       ...        ...        ...       ...              ...   
32158      CA  43.648206 -79.375239       372        43.647259   
32159      CA  43.649301 -79.376394       378        43.647259   
32160      CA  43.650077 -79.377312       379        43.647259   
32161      CA  43.649211 -79.376099       381        43.647259   
32162      CA  43.648089 -79.375313       388        43.647259   

       search_longitude  
0            -79.319796  
1            -79.319796  
2            -79.319796  
3            -79.319796  
4            -79.319796  
...                 ...  
32158        -79.379878  
32159        -79.379878  
32160        -79.379878  
32161        -79.379878  
32162        -79.379878  

[32163 rows x 10 columns]

In [13]:
df_fs.to_csv('df_foursquare.csv')

In [14]:
all_search_results_list

[                            name                            category  \
 0     Leslieville Farmers Market                      Farmers Market   
 1                     McDonald's                        Burger Joint   
 2               T.O. Ceviche Bar                 Peruvian Restaurant   
 3              Chalet Beauty Bar                          Hair Salon   
 4                    Chick-N-Joy                               Diner   
 5          Q Club Restaurant Bar              Arts and Entertainment   
 6                       Jaclyn's                Caribbean Restaurant   
 7              Rorschach Brewing                             Brewery   
 8           Canadian Drycleaners                         Dry Cleaner   
 9                         Subway                                Deli   
 10              Tulip Restaurant                               Diner   
 11                    Dulcinella                        Dessert Shop   
 12              Burrito Bandidos                  

In [15]:
# Call bike list

import requests

api_url = "http://api.citybik.es/v2/networks/bixi-toronto"
response = requests.get(api_url)
bixi_data = response.json()

bixi = bixi_data['network']
bixi_stations = bixi['stations']
bixi_station = bixi_stations[0]

toronto_bike_stations = []
i = 0

for station in bixi_stations:
    bixi_station = bixi_stations[i]
    bixi_name = bixi_station['name']
    bixi_lat = bixi_station['latitude']
    bixi_long = bixi_station['longitude']
    empty_slots = bixi_station['empty_slots']
    free_bikes = bixi_station['free_bikes']
    total_bikes = empty_slots + free_bikes

    bixi_dict = {'name' : bixi_name,
                 'latitude' : bixi_lat,
                 'longitude' : bixi_long,
                 'empty_slots' : empty_slots,
                 'free_bikes' : free_bikes,
                 'total_bikes' : total_bikes}
    
    toronto_bike_stations.append(bixi_dict)
    
    i += 1
    
df_to_bikes = pd.DataFrame(toronto_bike_stations)
df_to_bikes

name   latitude  longitude  \
0                 Queen St E / Woodward Ave  43.665269 -79.319796   
1               Primrose Ave / Davenport Rd  43.671420 -79.445947   
2                 Queen St. E / Rhodes Ave.  43.666224 -79.317693   
3                      Bond St / Queen St E  43.653236 -79.376716   
4                  Church St / Alexander St  43.663722 -79.380288   
..                                      ...        ...        ...   
690              Greenwood Ave / Sammon Ave  43.686987 -79.334782   
691                Lansdowne Subway Station  43.659229 -79.443209   
692                   Warden Subway Station  43.711611 -79.280556   
693  Kingston Rd / Scarborough Golf Club Rd  43.745311 -79.209707   
694                Wellington St W / Bay St  43.647259 -79.379878   

     empty_slots  free_bikes  total_bikes  
0              6          13           19  
1             15           0           15  
2             10          13           23  
3              8          13           21  
4             11          15           26  
..           ...         ...          ...  
690            8           3           11  
691            9          14           23  
692           11           8           19  
693            6           8           14  
694           23           3           26  

[695 rows x 6 columns]

In [16]:
df_fs['name'].value_counts()

Tim Hortons                               421
Subway                                    286
Starbucks                                 276
Aroma Espresso Bar                        224
Pizza Pizza                               140
                                         ... 
SOS Appliance Repair Inc                    1
Buco                                        1
Dale Construction Ltd                       1
Barry Macaffrey Carjor Sales Group Inc      1
Tropics Restaurant and Bar                  1
Name: name, Length: 5209, dtype: int64

In [17]:
df_fs

name                category     city region  \
0         Leslieville Farmers Market          Farmers Market  Toronto     ON   
1                         McDonald's            Burger Joint  Toronto     ON   
2                   T.O. Ceviche Bar     Peruvian Restaurant  Toronto     ON   
3                  Chalet Beauty Bar              Hair Salon  Toronto     ON   
4                        Chick-N-Joy                   Diner  Toronto     ON   
...                              ...                     ...      ...    ...   
32158                   Dog Fountain                Fountain  Toronto     ON   
32159     The Omni King Edward Hotel                   Hotel  Toronto     ON   
32160  Metropolitan Restaurant & Bar                   Diner  Toronto     ON   
32161                    Consort Bar  Arts and Entertainment  Toronto     ON   
32162                    Berczy Park              Urban Park  Toronto     ON   

      country   latitude  longitude  distance  search_latitude  \
0          CA  43.664679 -79.319687        40        43.665269   
1          CA  43.665065 -79.319000        62        43.665269   
2          CA  43.665973 -79.318863       108        43.665269   
3          CA  43.665973 -79.318863       108        43.665269   
4          CA  43.665121 -79.321347       129        43.665269   
...       ...        ...        ...       ...              ...   
32158      CA  43.648206 -79.375239       372        43.647259   
32159      CA  43.649301 -79.376394       378        43.647259   
32160      CA  43.650077 -79.377312       379        43.647259   
32161      CA  43.649211 -79.376099       381        43.647259   
32162      CA  43.648089 -79.375313       388        43.647259   

       search_longitude  
0            -79.319796  
1            -79.319796  
2            -79.319796  
3            -79.319796  
4            -79.319796  
...                 ...  
32158        -79.379878  
32159        -79.379878  
32160        -79.379878  
32161        -79.379878  
32162        -79.379878  

[32163 rows x 10 columns]

# Yelp

Send a request to Yelp with a small radius (1000m) for all the bike stations in your city of choice. 

In [18]:
YELP_KEY = os.getenv('YELP_KEY')

In [19]:
YELP_KEY = "Bearer Qr-3RHs9q19MPOGK_h2HhUzhKSu2JuByUWfy6MHRMVNfYSt69sPK23zmPkVFgKBHG3y40KZi6bxC5Pquq6_tcxE3CYc6Yy2HPfcYSe0C-4SK3d_ZlWCzs6sShgvtZHYx"

In [20]:
def yelp_call(query,latitude,longitude,radius):
    import requests

    url = f"https://api.yelp.com/v3/businesses/search?latitude={latitude}&longitude={longitude}&term={query}&radius={radius}&sort_by=distance&limit=50"

    headers = {
        "accept": "application/json",
        "Authorization": YELP_KEY
        }

    response = requests.get(url, headers=headers)

    yelp_data = response.json()

    return yelp_data

yelp_call('bar',43.664679,-79.319687,1000)

{'businesses': [{'id': 'iAEuxSiOjgandA3_xV-IQA',
   'alias': 'tulia-osteria-toronto',
   'name': 'Tulia Osteria',
   'image_url': 'https://s3-media4.fl.yelpcdn.com/bphoto/ha0Ry2rmU5Sk_7LwzyanJQ/o.jpg',
   'is_closed': False,
   'url': 'https://www.yelp.com/biz/tulia-osteria-toronto?adjust_creative=jxe0l4HW-9hSKcdBti6G6A&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=jxe0l4HW-9hSKcdBti6G6A',
   'review_count': 2,
   'categories': [{'alias': 'pizza', 'title': 'Pizza'},
    {'alias': 'italian', 'title': 'Italian'},
    {'alias': 'wine_bars', 'title': 'Wine Bars'}],
   'rating': 4.5,
   'coordinates': {'latitude': 43.66487, 'longitude': -79.32425},
   'transactions': [],
   'location': {'address1': '1402 Queen Street E',
    'address2': '',
    'address3': None,
    'city': 'Toronto',
    'zip_code': 'M4L 1C9',
    'country': 'CA',
    'state': 'ON',
    'display_address': ['1402 Queen Street E',
     'Toronto, ON M4L 1C9',
     'Canada']},
   'phone': '+14164616400'

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [21]:
# Check keys
yelp_data = yelp_call('bar',43.664679,-79.319687,1000)

In [22]:
businesses = yelp_data['businesses']
business_i = businesses[0]
business_i
business_i.keys()

dict_keys(['id', 'alias', 'name', 'image_url', 'is_closed', 'url', 'review_count', 'categories', 'rating', 'coordinates', 'transactions', 'location', 'phone', 'display_phone', 'distance'])

In [23]:
businesses[2]

{'id': '8EbtXXmu7F-gsOsR0xPmjg',
 'alias': 'lloyds-on-queen-toronto',
 'name': "Lloyd's On Queen",
 'image_url': '',
 'is_closed': False,
 'url': 'https://www.yelp.com/biz/lloyds-on-queen-toronto?adjust_creative=jxe0l4HW-9hSKcdBti6G6A&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=jxe0l4HW-9hSKcdBti6G6A',
 'review_count': 1,
 'categories': [{'alias': 'cocktailbars', 'title': 'Cocktail Bars'}],
 'rating': 5.0,
 'coordinates': {'latitude': 43.66380139616702,
  'longitude': -79.3283557134918},
 'transactions': [],
 'location': {'address1': '1298 Queen St E',
  'address2': '',
  'address3': None,
  'city': 'Toronto',
  'zip_code': 'M4L 1C4',
  'country': 'CA',
  'state': 'ON',
  'display_address': ['1298 Queen St E', 'Toronto, ON M4L 1C4', 'Canada']},
 'phone': '+14165518158',
 'display_phone': '+1 416-551-8158',
 'distance': 704.0903203850589}

In [24]:
# def parse_yelp_search(data):
#     search_results_list = []
#     i = 0
        
#     for business in businesses:
#         business_i = businesses[i]
#     # Set variables
#         business_id = business_i['id']

#         business_alias = business_i['alias']

#         business_name = business_i['name']

#         review_count = business_i['review_count']

#         categories = business_i['categories']
#         if len(categories) == 0:
#             category_1 = 'N/A'
#             category_1_alias = 'N/A'
#             category_2 = 'N/A'
#             category_2_alias = 'N/A'
#             category_3 = 'N/A'
#             category_3_alias = 'N/A'
#         elif len(categories) == 1:    
#             category_1 = categories[0]['title']
#             category_1_alias = categories[0]['alias']
#             category_2 = 'N/A'
#             category_2_alias = 'N/A'
#             category_3 = 'N/A'
#             category_3_alias = 'N/A'
#         elif len(categories) == 2:
#             category_1 = categories[0]['title']
#             category_1_alias = categories[0]['alias']
#             category_2 = categories[1]['title']
#             category_2_alias = categories[1]['alias']
#             category_3 = 'N/A'
#             category_3_alias = 'N/A'
#         elif len(categories) == 3:
#             category_1 = categories[0]['title']
#             category_1_alias = categories[0]['alias']
#             category_2 = categories[1]['title']
#             category_2_alias = categories[1]['alias']
#             category_3 = categories[2]['title']
#             category_3_alias = categories[2]['alias']

#         business_rating = business_i['rating']

#         coordinates = business_i['coordinates']
#         business_latitude = coordinates['latitude']
#         business_longitude = coordinates['longitude']

#         if 'price' in business_i:
#             business_price = len(business_i['price'])
#         else:
#             business_price = 'N/A'

#         business_location = business_i['location']
#         address1 = business_location['address1']
#         address2 = business_location['address2']
#         address3 = business_location['address3']
#         postal_code = business_location['zip_code']

#         business_phone = business_i['phone']
#         display_phone = business_i['display_phone']

#         search_latitude = yelp_data['region']['center']['latitude']
#         search_longitude = yelp_data['region']['center']['latitude']

#         distance_from_search = business_i['distance']

#         # Convert variables to dictionary
#         business_i_dict = {'name':business_name,
#                            'category_1':category_1,
#                            'business_rating':business_rating,
#                            'review_count':review_count,
#                            'distance_from_search':distance_from_search,
#                            'address1':address1,
#                             #'yelp_id':business_id, 
#                             #'alias':business_alias,
#                             #'subcategory_1':category_1_alias,
#                             #'category_2':category_2,
#                             #'subcategory_1':category_2_alias,
#                             #'category_3':category_3,
#                             #'subcategory_3':category_3_alias,
#                             'price':business_price,
#                             'business_latitude':business_latitude,
#                             'business_longitude':business_longitude,
#                             'search_latitude':search_latitude,
#                             'search_longitude':search_longitude,

#                              # 'address2':address2,
#                              # 'address3':address3,
#                              # 'postal_code':postal_code}
#                           }
        
#         # Append variable dictionary to list of dictionaries
#         search_results_list.append(business_i_dict)
        
#         # Iterate listing
#         i += 1
        
#     # Return the dataframe
#     return search_results_list

# parse_yelp_search(yelp_data)

In [25]:
# # Convert search result to dataframe
#     df_yelp_search_results = pd.DataFrame(search_results)

In [26]:
bixi_lats

[43.665269,
 43.67142,
 43.666224,
 43.653236,
 43.663722,
 43.657763,
 43.656729,
 43.664467,
 43.675492,
 43.674991,
 43.671944,
 43.662365,
 43.646144,
 43.663993,
 43.657266,
 43.6672144,
 43.673939,
 43.657991,
 43.66745,
 43.672453,
 43.6592088,
 43.689211,
 43.656927,
 43.658295,
 43.6940155,
 43.6809164,
 43.6910667,
 43.6975969,
 43.639832,
 43.667333,
 43.6480008,
 43.656518,
 43.687999,
 43.6563889,
 43.639179,
 43.6616667,
 43.66666667,
 43.657192,
 43.6576,
 43.660694,
 43.636533,
 43.659777,
 43.643667,
 43.666233,
 43.640114,
 43.653766,
 43.6538888888889,
 43.6508333333333,
 43.651238,
 43.6544915,
 43.6543604,
 43.635932,
 43.654501,
 43.634896,
 43.6314,
 43.636731,
 43.6534268,
 43.7112153,
 43.655227,
 43.685167,
 43.6704537,
 43.6691099,
 43.641389,
 43.643834,
 43.6545174,
 43.665846,
 43.6461,
 43.671349,
 43.667208,
 43.669328,
 43.672571,
 43.638497,
 43.662771,
 43.66852,
 43.652473,
 43.643975,
 43.651318,
 43.656094,
 43.670318,
 43.676667,
 43.640634,
 43.6

In [27]:
df_to_bikes[:5]

name   latitude  longitude  empty_slots  free_bikes  \
0    Queen St E / Woodward Ave  43.665269 -79.319796            6          13   
1  Primrose Ave / Davenport Rd  43.671420 -79.445947           15           0   
2    Queen St. E / Rhodes Ave.  43.666224 -79.317693           10          13   
3         Bond St / Queen St E  43.653236 -79.376716            8          13   
4     Church St / Alexander St  43.663722 -79.380288           11          15   

   total_bikes  
0           19  
1           15  
2           23  
3           21  
4           26

In [28]:
# df_yelp_listings.drop_duplicates()

In [29]:
# df_to_bikes

In [30]:
# df_yelp_listings.to_csv('df_yelp.csv')

In [31]:
# df_yelp_listings.value_counts('name')

Put your parsed results into a DataFrame

In [32]:
# all_yelp_results_list = []
df_concat = pd.DataFrame()

# List from bixi dataframe
bixi_lats = df_to_bikes['latitude'].to_list()
bixi_longs = df_to_bikes['longitude'].to_list()

bike_list_length = len(df_to_bikes)

for n in range(len(df_to_bikes)):
    bixi_lat = df_to_bikes.at[n,'latitude']
    bixi_long = df_to_bikes.at[n,'longitude']
    
# # For each bike station
# for lat in bixi_lats:
#     # Set lat and long to lat and long of current station
#     bixi_lat = bixi_lats[lat]
#     bixi_long = bixi_longs[lat]
#     print(bixi_lat)
#     print(bixi_long)
    query = 'bar'
    radius = 1000
# #     # Call API for each station's set of lat,long
    data = yelp_call(query,bixi_lat,bixi_long,radius)
    
    df = pd.json_normalize(data['businesses'])
    df['search_lat'] = bixi_lat
    df['search_long'] = bixi_long
    df_concat = pd.concat([df_concat,df])
    
    

    # Parse search results data
#     search_results = parse_yelp_search(data)
#     # Empty dataframe from previous result
#     df_search_results = pd.DataFrame()
#     # Create dataframe of search result
#     df_search_results = pd.DataFrame(search_results)
#     # Append search dataframe to list of all search dataframes
#     all_yelp_results_list.append(df_search_results)
#     n += 1

# df_yelp_listings = pd.concat(all_yelp_results_list, ignore_index = True)
# df_yelp_listings

/var/folders/j6/0rdcf97d7yv_pwm2sdy5zj940000gn/T/ipykernel_23804/1930075908.py:29: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_concat = pd.concat([df_concat,df])
/var/folders/j6/0rdcf97d7yv_pwm2sdy5zj940000gn/T/ipykernel_23804/1930075908.py:29: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_concat = pd.concat([df_concat,df])
/var/folders/j6/0rdcf97d7yv_pwm2sdy5zj940000gn/T/ipykernel_23804/1930075908.py:29: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df_concat = pd.concat([df_concat,df])
/var/folders/j6/0rdcf97d7yv_pwm2sdy5zj940000gn/T/ipykernel_23804/1930075908.py:29: FutureWarning: In a future ve

KeyError: 'businesses'

In [ ]:
df_reset_index = df_concat.reset_index(drop=True)
# df_concat.value_counts('name')
# filter_list = ['alias','name','review_count','search_lat','search_long']
# df_concat[filter_list].value_counts('alias')
df_cleaned = df_reset_index.drop(['image_url', 'is_closed', 'transactions', 'location.address2', 'location.address3', 'location.display_address'], axis=1)

In [ ]:
df_cleaned

In [ ]:
df_cleaned.to_csv('df_yelp_new.csv')

In [ ]:
df_yelp_duplicates = df_cleaned

In [ ]:
df_yelp_duplicates.to_csv('df_yelp_duplicates.csv')

In [ ]:
df_yelp_unique = df_cleaned.sort_values(by=['distance'])

In [ ]:
df_yelp_unique = df_yelp_unique.drop_duplicates(subset=['id'], keep='first')

In [ ]:
df_yelp_unique.to_csv('df_yelp_unique.csv')

In [ ]:
df_yelp_unique['review_count']

# Comparing Results

Which API provided you with more complete data? Provide an explanation. 

In [ ]:
# Count the number of attributes (columns) for each POI
num_attributes_yelp = df_yelp_unique.shape[1]
num_attributes_foursquare = df_fs.shape[1]

print(f"Number of attributes per POI from Yelp: {num_attributes_yelp}")
print(f"Number of attributes per POI from Foursquare: {num_attributes_foursquare}")

Get the top 10 restaurants according to their rating

In [ ]:
df_yelp_unique.sort_values(by =['rating','review_count'], ascending = False).head(10)

In [ ]:
# Calculate the geographic range covered by the POIs from Yelp and Foursquare
lat_range_yelp_unique = df_yelp_unique['coordinates.latitude'].max() - df_yelp_unique['coordinates.latitude'].min()
lon_range_yelp_unique = df_yelp_unique['coordinates.longitude'].max() - df_yelp_unique['coordinates.longitude'].min()

lat_range_fs = df_fs['latitude'].max() - df_fs['latitude'].min()
lon_range_fs = df_fs['longitude'].max() - df_fs['longitude'].min()

print(f"Latitude range covered by Yelp (Unique): {lat_range_yelp_unique}")
print(f"Longitude range covered by Yelp (Unique): {lon_range_yelp_unique}")
print(f"Latitude range covered by Foursquare: {lat_range_fs}")
print(f"Longitude range covered by Foursquare: {lon_range_fs}")
